<a href="https://colab.research.google.com/github/robert-sturrock/clue_board_game_solver/blob/main/CEA_Payroll_Giving_2023_full_workings.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Imports

In [277]:
import pandas as pd
import re
import numpy as np
import json
from google.colab.data_table import DataTable
%load_ext google.colab.data_table

# display more columns
DataTable.max_columns = 100
DataTable.max_rows = 10_000
DataTable.num_rows_per_page = 10

The google.colab.data_table extension is already loaded. To reload it, use:
  %reload_ext google.colab.data_table


## Helpful links

Schema doc: https://www.notion.so/centreforeffectivealtruism/Integrating-Payroll-Giving-with-Parfit-74bf2fb5cfb94a88b536b9a8d4a2334a

JSON file: https://drive.google.com/file/d/1-1Ynt_A7-MUaWy4drTrk66v5LgNCQoX9/view?usp=drive_link

R scripts and output: https://drive.google.com/drive/folders/1jtFp5FCo3KW74fofai1K9_BtiYIcfk1N

## JSON file structure example



```
{
    "payout_id": "9AMW4KFDVD",
    "recipient": "cea-uk",
    "gateway": "benevity",
    "invoice_date": "2023-07-01",
    "currency_code": "GBP",
    "amount": 10474.32,
    "payments": [
        {
            "person": {
                "email": "xxx@microsoft.com",
                "first_name": "xxx",
                "last_name": "xxxx",
                "address": "Not shared by donor",
                "city": "Not shared by donor",
                "state": "Not shared by donor",
                "postal_code": "EN1 2AW",
                "country": "UK"
            },
            "charge_currency_code": "GBP",
            "charge_amount": 100,
            "matched_amount": 100,
            "currency_code": "GBP",
            "fee": 0,
            "recipient": "cea_uk",
            "allocation": [
                {
                    "percentage": 50,
                    "organization": "founders-pledge-climate-change-fund"
                },
                {
                    "percentage": 50,
                    "organization": "global-development"
                }
            ],
            "gateway": "benevity",
            "payment_method": "payroll_giving",
            "donated_at": "2022-11-28 17:42:17",
            "metadata": {
                "matching": {
                    "type": "company_matching",
                    "company_name": "Microsoft"
                },
                "benevity": {
                    "cause_support_fee": 0,
                    "comment": "I would like equal parts of this recurring donation sent to (a) the Founders Pledge Climate Change Fund and (b) the Effective Altruism Globalh Health and Development Fund.",
                    "company": "Microsoft",
                    "fee_comment": "NA",
                    "merchant_fee": 0,
                    "project_remote": "NA",
                    "reason": "User Donation",
                    "source": "Payroll"
                }
            },
            "amount": 200,
            "net": 200
        }]
}
```



## Example python input dataframe

In [278]:
import pandas as pd

example_data = {
    "payout_id": ["9AMW4KFDVD"],
    "recipient": ["cea-uk"],
    "gateway": ["benevity"],
    "invoice_date": [pd.to_datetime("2023-07-01")],
    "currency_code": ["GBP"],
    "amount": [10474.32],
    "person_email": ["xxx@microsoft.com"],
    "person_first_name": ["xxx"],
    "person_last_name": ["xxxx"],
    "person_address": ["Not shared by donor"],
    "person_city": ["Not shared by donor"],
    "person_state": ["Not shared by donor"],
    "person_postal_code": ["EN1 2AW"],
    "person_country": ["UK"],
    "charge_currency_code": ["GBP"],
    "charge_amount": [100],
    "matched_amount": [100],
    "fee": [0],
    "allocation": [[
        {"organization": "founders-pledge-climate-change-fund", "percentage": 50},
        {"organization": "global-development", "percentage": 50}
    ]],
    "payment_method": ["payroll_giving"],
    "donated_at": [pd.to_datetime("2022-11-28 17:42:17")],
    "matching_type": ["company_matching"],
    "matching_company_name": ["Microsoft"],
    "benevity_cause_support_fee": [0],
    "benevity_comment": ["I would like equal parts..."],
    "benevity_company": ["Microsoft"],
    "benevity_fee_comment": ["NA"],
    "benevity_merchant_fee": [0],
    "benevity_project_remote": ["NA"],
    "benevity_reason": ["User Donation"],
    "benevity_source": ["Payroll"],
    "payments_amount": [200],
    "payments_net": [200]
}

example_df = pd.DataFrame(example_data)
example_df

payout_id recipient   gateway invoice_date currency_code    amount  \
0  9AMW4KFDVD    cea-uk  benevity   2023-07-01           GBP  10474.32   

        person_email person_first_name person_last_name       person_address  \
0  xxx@microsoft.com               xxx             xxxx  Not shared by donor   

   ... benevity_cause_support_fee             benevity_comment  \
0  ...                          0  I would like equal parts...   

  benevity_company benevity_fee_comment benevity_merchant_fee  \
0        Microsoft                   NA                     0   

   benevity_project_remote  benevity_reason  benevity_source payments_amount  \
0                       NA    User Donation          Payroll             200   

  payments_net  
0          200  

[1 rows x 33 columns]

## Structure

1. **Load data**: done through functions for each charity that load in the relevant files for the last quarter
2. **Clean data**: manipulate that data so that it is cleaned (ie all files follow a similar format), has a percentage allocation to all of the partner charities, and is easy for human review
3. **Manual Review**: Data is exported to a Google Sheet where Andy can review entries with a comment and ensure that they are allocated correctly
4. **Data transformation to JSON**: Final data is transformed into a JSON compatable format for upload into the GWWC database

## Approach

1. **Initial test**: Create a version of the code that works (for basic functions) for Benevity data and goes through these steps

## Functions

This section contains functions that are used throughout the code

### Benevity function

In [279]:
def benevity_data_load(drive_path):
  '''Loads in the Benevity csv files from a given drive folder path'''
  # file path and lines
  loaded_files = []
  charity_files_path = drive_path + "/" + charity + "/Reports/"

  # report header info
  start_line = 3
  end_line = 9
  for filename in os.listdir(charity_files_path):
        # convert files to csv - will only work with one type - this leads with csv
        try:

          # load the report metadata into a dictionary
          with open(file_path, 'r') as file:
              reader = csv.reader(file, delimiter=',')

              # Skip the lines before the desired start line
              for _ in range(start_line - 1):
                  next(reader)

              # Read and process the desired lines into a dictionary
              report_metadata = {}
              for line_number, row in enumerate(reader, start=start_line):
                  if line_number > end_line:
                      break
                  key, value = row
                  report_metadata[key] = value

          # load the actual data
          df_file = pd.read_csv(charity_files_path + filename, skiprows=11, dtype=str)

          # add the metadata from the top of the report
          df_file['payout_id'] = report_metadata['Disbursement ID']
          df_file['recipient'] = 'cea-uk'
          df_file['gateway'] = charity
          df_file['invoice_date'] = report_metadata['Period Ending']
          df_file['currency_code'] = report_metadata['Currency']

          # print names of converted files
          print("converted: " + filename)

          # append to other donation reports
          loaded_files.append(df_file)

        except:
          print("not convertable: " + filename)
          pass

  # put all reports together
  df = pd.concat(loaded_files)

  # clean out the irrelevant information in report
  irrelevant_rows = ['Totals','Total Donations (Gross)','Check Fee','Net Total Payment']
  df = df.loc[~df.Company.isin(irrelevant_rows)]

  return df



def benevity_data_clean(df):
  '''Cleans the benvity data in a pre-set way'''

  # clean existing column names
  df.columns = df.columns.str.lower().str.replace(' ','_')

  # replace NaN values with blanks
  df = df.replace(np.nan, '', regex=True)

  # create column mappings
  # person details
  person_column_mapping = {
      'donor_first_name': 'first_name',
      'donor_last_name': 'last_name',
      'email': 'email',
      'address': 'address',
      'city': 'city',
      'state/province': 'state',
      'postal_code': 'postal_code'
  }

  df = df.rename(columns = person_column_mapping)
  df['country'] = 'UK'

  # transaction details
  transaction_column_mapping = {
      'cause_support_fee':'cause_support_fee',
      'comment':'comment',
      'company':'matching_company_name',
      'currency':'charge_currency_code',
      'total_donation_to_be_acknowledged':'charge_amount',
      'donation_date':'donated_at',
      'project_remote_id':'project_remote',
      'match_amount':'matched_amount'
  }

  df = df.rename(columns = transaction_column_mapping)
  df['payment_method'] = 'payroll_giving'
  df['recurance'] = np.where(df.donation_frequency == 'Recurring', 'recurring', 'one-off')

  # convert certain columns to float (also requires removing ",")
  numeric_columns = ['merchant_fee','cause_support_fee','charge_amount','matched_amount']
  df[numeric_columns] = df[numeric_columns].apply(lambda x: pd.to_numeric(x.str.replace(',','')))

  # identify whether the row has a non-blank comment field (will generalize to other providers)
  # and will allow us to use this to flag fields for manual review even once project is
  # collapsed into the comment field
  df['has_comment'] = np.where(df['comment'].str.strip() != '', True, False)

  # make it so the project is listed under "comment" except when "comment" is populated
  df['comment'] = np.where(pd.isna(df.comment), df.project, df.comment)
  df['comment'] = df.comment.str.lower()

  # add missing transaction columns
  df['fee'] = df['merchant_fee'] + df['cause_support_fee']
  df['amount'] = df['charge_amount'] + df['matched_amount']
  df['net'] = df['amount'] - df['fee']
  df['allocation'] = None
  df['matching_type'] = 'company_matching'

  # reorder data
  vars = ['payout_id', 'recipient', 'gateway', 'invoice_date', 'currency_code',
        'amount', 'email', 'first_name', 'last_name',
        'address', 'city', 'state', 'postal_code',
        'country', 'charge_currency_code', 'charge_amount',
        'matched_amount', 'fee', 'allocation', 'payment_method', 'donated_at',
        'matching_type', 'matching_company_name', 'cause_support_fee',
        'comment','has_comment','fee_comment',
        'merchant_fee', 'project_remote', 'reason',
        'source', 'amount', 'net']

  df = df.loc[:,vars]

  return df


## Step 1: Load data


**Note**: At this stage you need to have added the folder with all the giving docs as a shortcut in your Google Drive. You'll ne

### Give access to your (EV) Google Drive

In [280]:
from google.colab import auth
auth.authenticate_user()

from google.auth import default
creds, _ = default()

# mount Google Drive
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [281]:
#@title Set drive filepath for giving reports

drive_path = "/content/drive/My Drive/Data Projects/CEA Payroll Giving/" #@param {type:"string"}
charity = "Benevity" #@param {type:"string"}

**Note:** relies on the files being along a drive path with the form: drive_path + charity + "/Reports/"

In [282]:
df = benevity_data_load(drive_path)
df.head()

converted: DonationReport_July_31_2022.csv
converted: DonationReport_Dec_9_2022_second.csv
converted: DonationReport_June_30_2022.csv
converted: DonationReport_Aug_31_2022.csv
converted: DonationReport_Dec_9_2022.csv
converted: DonationReport_Nov_4_2022.csv
converted: DonationReport_Sept_30_2022.csv
not convertable: DonationReport_Aug_31_2022.gsheet


Company                                        Project  \
0  TripAdvisor               EA Funds - Long-Term Future Fund   
1        Apple  EA Funds - Global Health and Development Fund   
2    Accenture                  CENTRE FOR EFFECTIVE ALTRUISM   
3     Google                   EA Funds - Animal Welfare Fund   
4     Google    EA Funds - Global Health and Development Fund   

          Donation Date     Donor First Name      Donor Last Name  \
0  2022-06-09T15:33:39Z  Not shared by donor  Not shared by donor   
1  2022-07-01T10:17:36Z                 Ekin               Sokmen   
2  2022-07-04T17:02:57Z           Frances M.               Tulley   
3  2022-07-07T11:15:36Z                 Vlad               Firoiu   
4  2022-07-26T13:59:15Z               Tamara            von Glehn   

                   Email                       Address                 City  \
0    Not shared by donor           Not shared by donor  Not shared by donor   
1  ekin.sokmen@apple.com  Flat 1, 3 Chiswick High Road               London   
2    Not shared by donor           Not shared by donor  Not shared by donor   
3      vladfi@google.com        48 St. Paul's Crescent               London   
4    tamaravg@google.com           Not shared by donor  Not shared by donor   

        State/Province Postal Code  ... Total Donation to be Acknowledged  \
0  Not shared by donor    OX14 3ZB  ...                            200.00   
1               London      W4 2ND  ...                            200.00   
2  Not shared by donor    SW12 0FF  ...                             20.00   
3                  NaN     NW1 9TN  ...                          7,510.00   
4  Not shared by donor     CB2 9HX  ...                            250.00   

  Match Amount Cause Support Fee Merchant Fee Fee Comment   payout_id  \
0       200.00             11.60         0.00         NaN  944HSFWVBH   
1       400.00              0.00         0.00         NaN  944HSFWVBH   
2         0.00              0.00         0.00         NaN  944HSFWVBH   
3     7,510.00              0.00       120.16         NaN  944HSFWVBH   
4       250.00              0.00         0.00         NaN  944HSFWVBH   

  recipient   gateway             invoice_date currency_code  
0    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP  
1    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP  
2    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP  
3    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP  
4    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP  

[5 rows x 28 columns]

## Step 2: Clean data

We need to make it so the data from Benevity contains (where possible) all the data that we want to put in the JSON file. For many charities the data will be more limited

In [283]:
df_benevity = benevity_data_clean(df)
df_benevity

payout_id recipient   gateway             invoice_date currency_code  \
0   944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
1   944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
2   944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
3   944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
4   944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
..         ...       ...       ...                      ...           ...   
68  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
69  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
70  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
71  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
72  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   

     amount                      email           first_name  \
0     400.0        Not shared by donor  Not shared by donor   
1     600.0      ekin.sokmen@apple.com                 Ekin   
2      20.0        Not shared by donor           Frances M.   
3   15020.0          vladfi@google.com                 Vlad   
4     500.0        tamaravg@google.com               Tamara   
..      ...                        ...                  ...   
68   1092.0    JOEDOUBLE@microsoft.com                  Joe   
69    100.0  JACKRICKARD@microsoft.com                 Jack   
70    100.0        Not shared by donor             Nicholas   
71    150.0        Not shared by donor                Fiona   
72    400.0        Not shared by donor  Not shared by donor   

              last_name                       address  ... cause_support_fee  \
0   Not shared by donor           Not shared by donor  ...              11.6   
1                Sokmen  Flat 1, 3 Chiswick High Road  ...               0.0   
2                Tulley           Not shared by donor  ...               0.0   
3                Firoiu        48 St. Paul's Crescent  ...               0.0   
4             von Glehn           Not shared by donor  ...               0.0   
..                  ...                           ...  ...               ...   
68               Double           Not shared by donor  ...               0.0   
69              Rickard           Not shared by donor  ...               0.0   
70               Brabbs           Not shared by donor  ...               0.0   
71               Corden           Not shared by donor  ...               0.0   
72  Not shared by donor           Not shared by donor  ...              11.6   

   comment has_comment fee_comment merchant_fee       project_remote  \
0                False                     0.00  3375395ed682dc35a26   
1                False                     0.00  3375355ed6826e5505d   
2                False                     0.00                        
3                False                   120.16  3375385ed682a7817cb   
4                False                     0.00  3375355ed6826e5505d   
..     ...         ...         ...          ...                  ...   
68               False                     0.00  3375355ed6826e5505d   
69               False                     0.00  3375355ed6826e5505d   
70               False                     0.00  3375355ed6826e5505d   
71               False                     0.00  3375395ed682dc35a26   
72               False                     0.00  3375395ed682dc35a26   

           reason    source   amount       net  
0   User Donation   Payroll    400.0    388.40  
1   User Donation  BlueSnap    600.0    600.00  
2   User Donation   Payroll     20.0     20.00  
3   User Donation  BlueSnap  15020.0  14899.84  
4   User Donation   Payroll    500.0    500.00  
..            ...       ...      ...       ...  
68  User Donation   Payroll   1092.0   1092.00  
69  User Donation   Payroll    100.0    100.00  
70  User Donation   Payroll    100.0    100.00  
71  Use

## Step 3: Merge all payroll giving data and clean

### Merge all charities

All the various payroll giving providers will be listed in here once the logic is complete

In [284]:
df = pd.concat([df_benevity])

### Specific Donor Preferences

At this stage we apply specific donor preferences where we have these available.

When they are avaiable we also add a variable indicating that we took them into account

In [285]:
# load in the income tracker spreadsheet
import gspread
gc = gspread.authorize(creds)
spreadsheet = gc.open('Income Tracker')


In [286]:
# load in donor data
sheet = spreadsheet.worksheet('Donor')
rows = sheet.get_all_values()
donors = pd.DataFrame.from_records(rows[1:], columns=rows[0])


Clean the naming conventions

In [287]:
donors.columns

Index(['First Name', 'Last Name', 'Full Name', 'Country', 'Provider',
       'Company', 'GHDF', 'AWF', 'LTFF', 'EAIF', 'Un', 'FP C', 'GW', 'CEA',
       'CATF', 'DMI', 'GWAGF', 'LLF', 'GFI', 'GWWC', 'GD', 'AMF', 'MC', 'GCRI',
       'SCI', 'EA DW', 'SS', 'ENDF', 'IGN', 'RC', '80K', 'CEIC', 'SI', 'WAI',
       'CLR', 'GovAI', 'JHCHS', 'CH', 'PHC', 'ALLFED', 'ACE R', 'ACE M',
       'FP GC', 'ACX', 'GEC', 'IL', '', 'Sum to 1?', '', 'Typical donation',
       'Reference'],
      dtype='object')

In [288]:
donors = donors.rename(columns={'First Name':'first_name','Last Name':'last_name'})
donors = donors.loc[:,
        ['first_name', 'last_name', 'Provider', 'GHDF', 'AWF', 'LTFF', 'EAIF', 'Un', 'FP C', 'GW', 'CEA',
       'CATF', 'DMI', 'GWAGF', 'LLF', 'GFI', 'GWWC', 'GD', 'AMF', 'MC', 'GCRI',
       'SCI', 'EA DW', 'SS', 'ENDF', 'IGN', 'RC', '80K', 'CEIC', 'SI', 'WAI',
       'CLR', 'GovAI', 'JHCHS', 'CH', 'PHC', 'ALLFED', 'ACE R', 'ACE M',
       'FP GC', 'ACX', 'GEC', 'IL']]
donors.head()

first_name   last_name                 Provider GHDF   AWF LTFF  EAIF Un  \
0       Adam  Clearwater        Charitable Giving    1                       
1   Alastair       Marsh              CAF Payroll  0.7  0.05  0.2  0.05      
2  Alexander       Merry              CAF Payroll    1                       
3   Alistair      Nelson        CAF Direct giving  0.5   0.3  0.1            
4       Amar       Radia  Charities Trust Payroll    1                       

  FP C GW  ... JHCHS   CH PHC ALLFED ACE R ACE M FP GC ACX GEC IL  
0          ...                                                     
1          ...                                                     
2          ...                                                     
3          ...        0.1                                          
4          ...                                                     

[5 rows x 43 columns]

Left join the donor spreadsheet onto the dataset

In [289]:
df = df.merge(donors, how='left', indicator="donor_match")
df['donor_match'] = np.where(df.donor_match=='left_only','No','Yes')

In [290]:
df

payout_id recipient   gateway             invoice_date currency_code  \
0    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
1    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
2    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
3    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
4    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
..          ...       ...       ...                      ...           ...   
473  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
474  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
475  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
476  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
477  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   

      amount                      email           first_name  \
0      400.0        Not shared by donor  Not shared by donor   
1      600.0      ekin.sokmen@apple.com                 Ekin   
2       20.0        Not shared by donor           Frances M.   
3    15020.0          vladfi@google.com                 Vlad   
4      500.0        tamaravg@google.com               Tamara   
..       ...                        ...                  ...   
473   1092.0    JOEDOUBLE@microsoft.com                  Joe   
474    100.0  JACKRICKARD@microsoft.com                 Jack   
475    100.0        Not shared by donor             Nicholas   
476    150.0        Not shared by donor                Fiona   
477    400.0        Not shared by donor  Not shared by donor   

               last_name                       address  ...   CH  PHC ALLFED  \
0    Not shared by donor           Not shared by donor  ...  NaN  NaN    NaN   
1                 Sokmen  Flat 1, 3 Chiswick High Road  ...  NaN  NaN    NaN   
2                 Tulley           Not shared by donor  ...  NaN  NaN    NaN   
3                 Firoiu        48 St. Paul's Crescent  ...  NaN  NaN    NaN   
4              von Glehn           Not shared by donor  ...  NaN  NaN    NaN   
..                   ...                           ...  ...  ...  ...    ...   
473               Double           Not shared by donor  ...  NaN  NaN    NaN   
474              Rickard           Not shared by donor  ...  NaN  NaN    NaN   
475               Brabbs           Not shared by donor  ...  NaN  NaN    NaN   
476               Corden           Not shared by donor  ...  NaN  NaN    NaN   
477  Not shared by donor           Not shared by donor  ...  NaN  NaN    NaN   

    ACE R ACE M  FP GC  ACX  GEC   IL donor_match  
0     NaN   NaN    NaN  NaN  NaN  NaN          No  
1     NaN   NaN    NaN  NaN  NaN  NaN          No  
2     NaN   NaN    NaN  NaN  NaN  NaN          No  
3     NaN   NaN    NaN  NaN  NaN  NaN          No  
4     NaN   NaN    NaN  NaN  NaN  NaN          No  
..    ...   ...    ...  ...  ...  ...         ...  
473   NaN   NaN    NaN  NaN  NaN  NaN          No  
474   NaN   NaN    NaN  NaN  NaN  NaN          No  
475   NaN   NaN    NaN  NaN  NaN  NaN          No  
476   NaN   NaN    NaN  NaN  NaN  NaN          No  
477   NaN   NaN    NaN  NaN  NaN  NaN          No  

[478 rows x 75 columns]

### Apply logic to map comments / projects to codes

We will add four new columns:
* Project (guess)
* Restriction (guess)
* Multiple: flagged if we suspect row needs to be broken out to multiple
* Look at: to signal bookkeeper should pay special attention

General cleaning:
* Make the input all lower case

Important fields for guesses:

*Project*: Can take values: CEA General, EA Funds, GWWC. Others?
* If contains EA Funds --> EA funds
* If contains "Global" or "development" --> EA funds
* If contains "Long" --> EA funds
* If blank / NaN: CEA General
* If "Centre for effective": CEA General

*Restriction*:
* for all EA Funds, just use the value for Charitable Giving - format1

*Multiple*:
* If field contains a number then it probably requires multiple rows

*Flag*:
* If contains multiple then flag
* If cell is not blank, and isn't allocated


Extra info: I can probably use [DataFrame.explode()](https://stackoverflow.com/questions/27263805/pandas-column-of-lists-create-a-row-for-each-list-element) to create multiple rows



Abbreviation	Project	Restriction
GHDF	233 Global Development Fund	EA Funds Grantmaking
AWF	231 Animal Welfare Fund	EA Funds Grantmaking
LTFF	234 Long-term Future Fund	EA Funds Grantmaking
EAIF	232 EA Infrastructure Fund	EA Funds Grantmaking
DMI	812 Development Media International (DMI)	EA Funds Grantmaking
FP Climate	821 Founders Pledge Climate Fund (FPCF)	EA Funds Grantmaking
GFI	825 Good Food Institute (GFI)	EA Funds Grantmaking
GW	823 GiveWell current recommendation (GW)	EA Funds Grantmaking
CEA	100 CEA General	CEA
CATF	809 Clean Air Task Force (CATF)	EA Funds Grantmaking
Un	000 Unrestricted	Unrestricted
GWWC	210 GWWC	GWWC
GD	822 GiveDirectly (GD)	EA Funds Grantmaking

In [291]:
def categorize_restriction(df):
  '''categorize restiction based on guesses from individual comment
  where provided'''
  # categorize blanks as CEA
  # note: ^ specifies no values before this, $ means none after
  if bool(re.search(r'^\s*$', df['comment'])):
    return 'Unrestricted'
  if 'centre' in df['comment']:
    return 'CEA'

  # categorize GWWC:
  if 'giving what' in df['comment']:
    return 'GWWC'

  # categorize EAF:
  keywords = ['funds','global','animal welfare','development','long','ltf ','health','meta','givewell','gw','malaria','amf','infra','deworm the world','evidence', 'clean air', 'food']
  if any(keyword in df['comment'] for keyword in keywords):
    return 'EA Funds'

  # categorize "please do not send any mailings"
  if 'please do not send any mailings' in df['comment']:
    return 'Unrestricted'

  # leave rest uncategorized
  else:
    return ''

In [292]:
def categorize_project(df):
  '''categorize project based on guesses from individual comment
  where provided'''
  # categorize blanks as CEA
  # note: ^ specifies no values before this, $ means none after
  if df['restriction'] == 'Unrestricted':
    return '000 Unrestricted'

  if df['restriction'] == 'CEA':
    return '100 CEA General'

  # categorize GWWC:
  if df['restriction'] == 'GWWC':
    return '210 GWWC'

  # categorize EAF:
  if df['restriction'] == 'EA Funds':
    if ('development' in df['comment']) or ('health' in df['comment']):
      return '233 Global Development Fund'
    if 'food' in df['comment']:
      return '825 Good Food Institute (GFI)'
    if 'animal welfare' in df['comment']:
      return '231 Animal Welfare Fund'
    if ('infra' in df['comment']) or ('meta' in df['comment']):
      return '232 EA Infrastructure Fund'
    if ('long' in df['comment']) or ('ltf ' in df['comment']):
      return '234 Long-term Future Fund'
    if ('gw' in df['comment']) or ('givewell ' in df['comment']):
      return '823 GiveWell current recommendation (GW)'
    if ('malaria' in df['comment']) or ('amf ' in df['comment']):
      return '803 Against Malaria Foundation (AMF)'
    if ('deworm the world' in df['comment']) or ('evidence' in df['comment']):
      return '817 Evidence Action (Deworm the World)'
    if ('clean air' in df['comment']):
      return '809 Clean Air Task Force (CATF)'
    if ('animal charity' in df['comment']):
      return 'Animal Charity Evaluators related'
    else:
      return ''
  # leave rest uncategorized
  else:
    return ''

In [293]:
def identify_multiple(df):
  '''used to flag when we think an comment contains multiple EA orgs and
  needs a more complicated allocation'''
  # set up count to record instances of likely EA orgs in comment
  count = 0

  # anytime a number is referenced we should think multiple
  if bool(re.search(r'\d', df['comment'])):
    count = 2

  # anytime we see EA keywords we should add 1 to count
  # need to do this by initiative so we don't double count "global", "health"
  if df['restriction'] == 'EA Funds':
    if ('development' in df['comment']) or ('health' in df['comment']):
      count +=1
    if 'food' in df['comment']:
      count +=1
    if 'animal welfare' in df['comment']:
      count +=1
    if ('infra' in df['comment']) or ('meta' in df['comment']):
      count +=1
    if ('long' in df['comment']) or ('ltf ' in df['comment']):
      count +=1
    if ('gw' in df['comment']) or ('givewell ' in df['comment']):
      count +=1
    if ('malaria' in df['comment']) or ('amf ' in df['comment']):
      count +=1
    if ('deworm the world' in df['comment']) or ('evidence' in df['comment']):
      count +=1
    if ('clean air' in df['comment']):
      count +=1


  # count variable won't be that reliable (since we flag #s and words) so just
  # record if it's greater than one
  if count > 1:
    return '**Maybe**'
  else:
    return 'No'


In [294]:
def identify_flag(df):

  # if any comment then review
  if df['has_comment'] == True:
    return "Review"

  else:
    return ""

In [295]:
df

payout_id recipient   gateway             invoice_date currency_code  \
0    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
1    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
2    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
3    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
4    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
..          ...       ...       ...                      ...           ...   
473  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
474  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
475  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
476  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
477  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   

      amount                      email           first_name  \
0      400.0        Not shared by donor  Not shared by donor   
1      600.0      ekin.sokmen@apple.com                 Ekin   
2       20.0        Not shared by donor           Frances M.   
3    15020.0          vladfi@google.com                 Vlad   
4      500.0        tamaravg@google.com               Tamara   
..       ...                        ...                  ...   
473   1092.0    JOEDOUBLE@microsoft.com                  Joe   
474    100.0  JACKRICKARD@microsoft.com                 Jack   
475    100.0        Not shared by donor             Nicholas   
476    150.0        Not shared by donor                Fiona   
477    400.0        Not shared by donor  Not shared by donor   

               last_name                       address  ...   CH  PHC ALLFED  \
0    Not shared by donor           Not shared by donor  ...  NaN  NaN    NaN   
1                 Sokmen  Flat 1, 3 Chiswick High Road  ...  NaN  NaN    NaN   
2                 Tulley           Not shared by donor  ...  NaN  NaN    NaN   
3                 Firoiu        48 St. Paul's Crescent  ...  NaN  NaN    NaN   
4              von Glehn           Not shared by donor  ...  NaN  NaN    NaN   
..                   ...                           ...  ...  ...  ...    ...   
473               Double           Not shared by donor  ...  NaN  NaN    NaN   
474              Rickard           Not shared by donor  ...  NaN  NaN    NaN   
475               Brabbs           Not shared by donor  ...  NaN  NaN    NaN   
476               Corden           Not shared by donor  ...  NaN  NaN    NaN   
477  Not shared by donor           Not shared by donor  ...  NaN  NaN    NaN   

    ACE R ACE M  FP GC  ACX  GEC   IL donor_match  
0     NaN   NaN    NaN  NaN  NaN  NaN          No  
1     NaN   NaN    NaN  NaN  NaN  NaN          No  
2     NaN   NaN    NaN  NaN  NaN  NaN          No  
3     NaN   NaN    NaN  NaN  NaN  NaN          No  
4     NaN   NaN    NaN  NaN  NaN  NaN          No  
..    ...   ...    ...  ...  ...  ...         ...  
473   NaN   NaN    NaN  NaN  NaN  NaN          No  
474   NaN   NaN    NaN  NaN  NaN  NaN          No  
475   NaN   NaN    NaN  NaN  NaN  NaN          No  
476   NaN   NaN    NaN  NaN  NaN  NaN          No  
477   NaN   NaN    NaN  NaN  NaN  NaN          No  

[478 rows x 75 columns]

In [296]:
df['restriction'] = df.apply(categorize_restriction, axis=1)
df['project'] = df.apply(categorize_project, axis=1)
df['multiple'] = df.apply(identify_multiple, axis=1)
df['flag'] = df.apply(identify_flag, axis=1)


In [297]:
df.loc[df.flag=='Review',"comment":]

comment  has_comment  \
25   hi!  i'd like to make this recurring donation ...         True   
59   i would like equal parts of this recurring don...         True   
60                50% global dev, 50% long-term future         True   
61   hi, here is the information i need to provide ...         True   
62   hi, here is the information i need to provide ...         True   
..                                                 ...          ...   
464  hi, here is the information i need to provide ...         True   
465  hi, here is the information i need to provide ...         True   
466  hi, here is the information i need to provide ...         True   
468  email: sunnycarter@microsoft.com fund - founde...         True   
469  hi, here is the information i need to provide ...         True   

    fee_comment  merchant_fee project_remote         reason   source  amount  \
25                        0.0                 User Donation  Payroll   858.0   
59                        0.0                 User Donation  Payroll   200.0   
60                        0.0                 User Donation  Payroll   200.0   
61                        0.0                 User Donation  Payroll  1200.0   
62                        0.0                 User Donation  Payroll   360.0   
..          ...           ...            ...            ...      ...     ...   
464                       0.0                 User Donation  Payroll   400.0   
465                       0.0                 User Donation  Payroll    40.0   
466                       0.0                 User Donation  Payroll   400.0   
468                       0.0                 User Donation  Payroll    74.0   
469                       0.0                 User Donation  Payroll    20.0   

        net     Provider  ... ACE M FP GC  ACX  GEC   IL donor_match  \
25    858.0  Benevity CG  ...                                    Yes   
59    200.0  Benevity CG  ...                                    Yes   
60    200.0  Benevity CG  ...                                    Yes   
61   1200.0  Benevity CG  ...                                    Yes   
62    360.0          NaN  ...   NaN   NaN  NaN  NaN  NaN          No   
..      ...          ...  ...   ...   ...  ...  ...  ...         ...   
464   400.0  Benevity CG  ...                                    Yes   
465    40.0  Benevity CG  ...                                    Yes   
466   400.0  Benevity CG  ...                                    Yes   
468    74.0  Benevity CG  ...                                    Yes   
469    20.0  Benevity CG  ...                                    Yes   

    restriction                                   project   multiple    flag  
25     EA Funds                                                   No  Review  
59     EA Funds               233 Global Development Fund         No  Review  
60     EA Funds                 234 Long-term Future Fund  **Maybe**  Review  
61     EA Funds  823 GiveWell current recommendation (GW)  **Maybe**  Review  
62                                                         **Maybe**  Review  
..          ...                                       ...        ...     ...  
464                                                        **Maybe**  Review  
465    EA Funds                 234 Long-term Future Fund         No  Review  
466                                                        **Maybe**  Review  
468                                                        **Maybe**  Review  
469                                                        **Maybe**  Review  

[62 rows x 55 columns]

### Add allocations for cases where donor information doesn't exist

This specifically covers cases where we guess a single allocation

First we set up the reference table

In [298]:
sheet = spreadsheet.worksheet('Ref')
rows = sheet.get_all_values()
ref = pd.DataFrame.from_records(rows[2:], columns=rows[1])

# simplify column names
ref.columns = ref.columns.str.lower()

In [299]:
ref

abbreviation                                            project  \
0           AMF               803 Against Malaria Foundation (AMF)   
1           80K                                   200 80,000 Hours   
2        ALLFED                                         804 ALLFED   
3           AWF                            231 Animal Welfare Fund   
4          CATF                    809 Clean Air Task Force (CATF)   
5           CEA                                    100 CEA General   
6          CEIC  806 CE Incubated charities - Charity Entrepren...   
7            CH                               140 Community Health   
8           CLR                 807 Center on Long-Term Risk (CLR)   
9           DMI          812 Development Media International (DMI)   
10        EA DW             817 Evidence Action (Deworm the World)   
11         EAIF                         232 EA Infrastructure Fund   
12         ENDF                           816 END Fund (deworming)   
13         FP C            821 Founders Pledge Climate Fund (FPCF)   
14         GCRI      824 Global Catastrophic Risk Institute (GCRI)   
15           GD                              822 GiveDirectly (GD)   
16          GFI                      825 Good Food Institute (GFI)   
17         GHDF                        233 Global Development Fund   
18        GovAI                                          240 GovAI   
19           GW           823 GiveWell current recommendation (GW)   
20         GWWC                                           210 GWWC   
21          IGN                    829 Iodine Global Network (IGN)   
22        JHCHS       831 Johns Hopkins Center for Health Security   
23         LTFF                          234 Long-term Future Fund   
24           MC                             833 Malaria Consortium   
25          PHC                 837 Project Healthy Children (PHC)   
26           RC                                839 Rethink Charity   
27          SCI       841 Schistosomiasis Control Initiative (SCI)   
28           SI                       842 Sentience Institute (SI)   
29           SS                        843 Sightsavers (deworming)   
30           Un                                   000 Unrestricted   
31          WAI                         846 Wild Animal Initiative   
32        GWAGF                     867 GiveWell (All Grants Fund)   
33          LLF                      237 Longview Longtermism Fund   
34        ACE R  802 ACE Recommendations - Animal Charity Evalu...   
35        ACE M  851 ACE Movement Grants - Animal Charity Evalu...   
36        FP GC  865 Founders Pledge Global Catastrophic Risks ...   
37          ACX                                     857 ACX Grants   
38          GEC                         872 Good Energy Collective   
39           IL                               875 Industrious Labs   

             restriction                                     parfitslug  
0   EA Funds Grantmaking                     against-malaria-foundation  
1     80,000 Hours (80K)                                    80000-hours  
2   EA Funds Grantmaking        alliance-to-feed-the-earth-in-disasters  
3   EA Funds Grantmaking                                 animal-welfare  
4   EA Funds Grantmaking                           clean-air-task-force  
5                   CEA                   centre-for-effective-altruism  
6   EA Funds Grantmaking              charity-entrepreneurship-projects  
7                    CEA                                                 
8   EA Funds Grantmaking             stiftung-fur-effektiven-altruismus  
9   EA Funds Grantmaking                development-media-international  
10  EA Funds Grantmaking                    deworm-the-world-initiative  
11  EA Funds Grantmaking                                   ea-community  
12  EA Funds Grantmaking                                       end-fund  
13  EA Funds Grantmaking            founders-pledge-climate-change-fund  
14  EA Funds Grantmaki

In [300]:
df.head()

payout_id recipient   gateway             invoice_date currency_code  \
0  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
1  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
2  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
3  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
4  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   

    amount                  email           first_name            last_name  \
0    400.0    Not shared by donor  Not shared by donor  Not shared by donor   
1    600.0  ekin.sokmen@apple.com                 Ekin               Sokmen   
2     20.0    Not shared by donor           Frances M.               Tulley   
3  15020.0      vladfi@google.com                 Vlad               Firoiu   
4    500.0    tamaravg@google.com               Tamara            von Glehn   

                        address  ... ACE M FP GC  ACX  GEC   IL  donor_match  \
0           Not shared by donor  ...   NaN   NaN  NaN  NaN  NaN           No   
1  Flat 1, 3 Chiswick High Road  ...   NaN   NaN  NaN  NaN  NaN           No   
2           Not shared by donor  ...   NaN   NaN  NaN  NaN  NaN           No   
3        48 St. Paul's Crescent  ...   NaN   NaN  NaN  NaN  NaN           No   
4           Not shared by donor  ...   NaN   NaN  NaN  NaN  NaN           No   

    restriction           project multiple flag  
0  Unrestricted  000 Unrestricted       No       
1  Unrestricted  000 Unrestricted       No       
2  Unrestricted  000 Unrestricted       No       
3  Unrestricted  000 Unrestricted       No       
4  Unrestricted  000 Unrestricted       No       

[5 rows x 79 columns]

In [301]:
# make all allocation columns numeric
df.loc[:, 'GHDF':'IL'] = df.loc[:, 'GHDF':'IL'].applymap(pd.to_numeric)

# check the current sum for each row allocation
df['allocation_sum_check'] = df.loc[:, 'GHDF':'IL'].sum(axis=1, skipna=True)
df.allocation_sum_check.describe()

<ipython-input-301-4537d52616be>:2: DeprecationWarning: In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[df.columns[i]] = newvals` or, if columns are non-unique, `df.isetitem(i, newvals)`
  df.loc[:, 'GHDF':'IL'] = df.loc[:, 'GHDF':'IL'].applymap(pd.to_numeric)


count    478.000000
mean       0.161088
std        0.367997
min        0.000000
25%        0.000000
50%        0.000000
75%        0.000000
max        1.000000
Name: allocation_sum_check, dtype: float64

In [302]:
def allocate(row, ref_df):
    # find the project in the reference dataframe
    project_row = ref_df.loc[ref_df['project'] == row['project']]
    if not project_row.empty and row['allocation_sum_check'] == 0:
        # if project found, and there isn't currently an allocation, get the abbreviation
        abbreviation = project_row['abbreviation'].values[0]
        if abbreviation in row.index:
            # if the abbreviation is a column in the main dataframe, set its value to 1
            row[abbreviation] = 1
    return row


# apply the function to each row in the dataframe
df = df.apply(lambda row: allocate(row, ref), axis=1)

In [303]:
df

payout_id recipient   gateway             invoice_date currency_code  \
0    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
1    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
2    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
3    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
4    944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
..          ...       ...       ...                      ...           ...   
473  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
474  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
475  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
476  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
477  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   

      amount                      email           first_name  \
0      400.0        Not shared by donor  Not shared by donor   
1      600.0      ekin.sokmen@apple.com                 Ekin   
2       20.0        Not shared by donor           Frances M.   
3    15020.0          vladfi@google.com                 Vlad   
4      500.0        tamaravg@google.com               Tamara   
..       ...                        ...                  ...   
473   1092.0    JOEDOUBLE@microsoft.com                  Joe   
474    100.0  JACKRICKARD@microsoft.com                 Jack   
475    100.0        Not shared by donor             Nicholas   
476    150.0        Not shared by donor                Fiona   
477    400.0        Not shared by donor  Not shared by donor   

               last_name                       address  ... FP GC ACX GEC  IL  \
0    Not shared by donor           Not shared by donor  ...   NaN NaN NaN NaN   
1                 Sokmen  Flat 1, 3 Chiswick High Road  ...   NaN NaN NaN NaN   
2                 Tulley           Not shared by donor  ...   NaN NaN NaN NaN   
3                 Firoiu        48 St. Paul's Crescent  ...   NaN NaN NaN NaN   
4              von Glehn           Not shared by donor  ...   NaN NaN NaN NaN   
..                   ...                           ...  ...   ...  ..  ..  ..   
473               Double           Not shared by donor  ...   NaN NaN NaN NaN   
474              Rickard           Not shared by donor  ...   NaN NaN NaN NaN   
475               Brabbs           Not shared by donor  ...   NaN NaN NaN NaN   
476               Corden           Not shared by donor  ...   NaN NaN NaN NaN   
477  Not shared by donor           Not shared by donor  ...   NaN NaN NaN NaN   

    donor_match   restriction           project  multiple flag  \
0            No  Unrestricted  000 Unrestricted        No        
1            No  Unrestricted  000 Unrestricted        No        
2            No  Unrestricted  000 Unrestricted        No        
3            No  Unrestricted  000 Unrestricted        No        
4            No  Unrestricted  000 Unrestricted        No        
..          ...           ...               ...       ...  ...   
473          No  Unrestricted  000 Unrestricted        No        
474          No  Unrestricted  000 Unrestricted        No        
475          No  Unrestricted  000 Unrestricted        No        
476          No  Unrestricted  000 Unrestricted        No        
477          No  Unrestricted  000 Unrestricted        No        

    allocation_sum_check  
0                    0.0  
1                    0.0  
2                    0.0  
3                    0.0  
4                    0.0  
..                   ...  
473                  0.0  
474                  0.0  
475                  0.0  
476                  0.0  
477                  0.0  

[478 rows x 80 columns]

## Step 4: Output to Google sheet for review

Output the data to a Google sheet where Andy can review

In [304]:
from gspread_dataframe import set_with_dataframe
df = df.sort_values(by=['gateway','invoice_date', 'last_name','first_name'])
spreadsheet = gc.open('Quarterly Payroll Giving Intermediate Reports')
sheet = spreadsheet.worksheet('2023 Q1')
set_with_dataframe(sheet, df)

## Step 5: Convert file to JSON

### Load back in Google sheet

First load (the now edited) Google sheet back into Colab and then convert to JSON

In [305]:
# load in the google sheet data
spreadsheet = gc.open('Quarterly Payroll Giving Intermediate Reports')
sheet = spreadsheet.worksheet('2023 Q1')
rows = sheet.get_all_values()
df = pd.DataFrame.from_records(rows[1:], columns=rows[0])


In [306]:
df.head()

payout_id recipient   gateway             invoice_date currency_code  \
0  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
1  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
2  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
3  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
4  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   

  amount                               email first_name   last_name  \
0    750            r.abernethy@elsevier.com     Robert   Abernethy   
1    400  Ole.Andreassen@Rothschildandco.com        Ole  Andreassen   
2    400  Ole.Andreassen@Rothschildandco.com        Ole  Andreassen   
3   5100  Ole.Andreassen@Rothschildandco.com        Ole  Andreassen   
4    100              courtneyant@google.com   Courtney    Antrobus   

                  address  ... FP GC ACX GEC IL donor_match   restriction  \
0   22 Stevenson Crescent  ...                           No  Unrestricted   
1  Long Lane 239, Flat 40  ...                           No  Unrestricted   
2  Long Lane 239, Flat 40  ...                           No  Unrestricted   
3     Not shared by donor  ...                           No  Unrestricted   
4     Not shared by donor  ...                           No  Unrestricted   

            project multiple flag allocation_sum_check  
0  000 Unrestricted       No                         0  
1  000 Unrestricted       No                         0  
2  000 Unrestricted       No                         0  
3  000 Unrestricted       No                         0  
4  000 Unrestricted       No                         0  

[5 rows x 80 columns]

### Checks

Checks:
1. Do all the allocations sum to 100%?


In [307]:
# Checking whether the sum of the values in columns sum_columns sums to 1
df.loc[:, 'GHDF':'IL'] = df.loc[:, 'GHDF':'IL'].applymap(pd.to_numeric)
df['sum_check'] = df.loc[:, 'GHDF':'IL'].sum(axis=1, skipna=True)
df.loc[df.sum_check != 1]

payout_id recipient   gateway             invoice_date currency_code  \
194  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
237  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
248  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
251  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
253  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
265  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
269  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
280  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
283  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
309  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   
324  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   

     amount                email           first_name            last_name  \
194  335.49      nlim@google.com             Nicholas                  Lim   
237     360  Not shared by donor  Not shared by donor  Not shared by donor   
248     360  Not shared by donor  Not shared by donor  Not shared by donor   
251     400  Not shared by donor  Not shared by donor  Not shared by donor   
253      74  Not shared by donor  Not shared by donor  Not shared by donor   
265     360  Not shared by donor  Not shared by donor  Not shared by donor   
269      74  Not shared by donor  Not shared by donor  Not shared by donor   
280     360  Not shared by donor  Not shared by donor  Not shared by donor   
283      74  Not shared by donor  Not shared by donor  Not shared by donor   
309     360  Not shared by donor  Not shared by donor  Not shared by donor   
324     360  Not shared by donor  Not shared by donor  Not shared by donor   

                 address  ...  ACX  GEC   IL donor_match restriction project  \
194  Not shared by donor  ...  NaN  NaN  NaN          No                       
237  Not shared by donor  ...  NaN  NaN  NaN          No                       
248  Not shared by donor  ...  NaN  NaN  NaN          No                       
251  Not shared by donor  ...  NaN  NaN  NaN          No                       
253  Not shared by donor  ...  NaN  NaN  NaN          No                       
265  Not shared by donor  ...  NaN  NaN  NaN          No                       
269  Not shared by donor  ...  NaN  NaN  NaN          No                       
280  Not shared by donor  ...  NaN  NaN  NaN          No                       
283  Not shared by donor  ...  NaN  NaN  NaN          No                       
309  Not shared by donor  ...  NaN  NaN  NaN          No                       
324  Not shared by donor  ...  NaN  NaN  NaN          No                       

      multiple    flag allocation_sum_check sum_check  
194         No  Review                    0       0.0  
237  **Maybe**  Review                    0       0.0  
248  **Maybe**  Review                    0       0.0  
251  **Maybe**  Review                    0       0.0  
253  **Maybe**  Review                    0       0.0  
265  **Maybe**  Review                    0       0.0  
269  **Maybe**  Review                    0       0.0  
280  **Maybe**  Review                    0       0.0  
283  **Maybe**  Review                    0       0.0  
309  **Maybe**  Review                    0       0.0  
324  **Maybe**  Review                    0       0.0  

[11 rows x 81 columns]

### Parfit

Load in the table of assignments. Goal here is if

In [308]:
spreadsheet = gc.open('Income Tracker')
sheet = spreadsheet.worksheet('Ref')
rows = sheet.get_all_values()
ref = pd.DataFrame.from_records(rows[2:], columns=rows[1])

# simplify column names
ref.columns = ref.columns.str.lower()

In [309]:
ref

abbreviation                                            project  \
0           AMF               803 Against Malaria Foundation (AMF)   
1           80K                                   200 80,000 Hours   
2        ALLFED                                         804 ALLFED   
3           AWF                            231 Animal Welfare Fund   
4          CATF                    809 Clean Air Task Force (CATF)   
5           CEA                                    100 CEA General   
6          CEIC  806 CE Incubated charities - Charity Entrepren...   
7            CH                               140 Community Health   
8           CLR                 807 Center on Long-Term Risk (CLR)   
9           DMI          812 Development Media International (DMI)   
10        EA DW             817 Evidence Action (Deworm the World)   
11         EAIF                         232 EA Infrastructure Fund   
12         ENDF                           816 END Fund (deworming)   
13         FP C            821 Founders Pledge Climate Fund (FPCF)   
14         GCRI      824 Global Catastrophic Risk Institute (GCRI)   
15           GD                              822 GiveDirectly (GD)   
16          GFI                      825 Good Food Institute (GFI)   
17         GHDF                        233 Global Development Fund   
18        GovAI                                          240 GovAI   
19           GW           823 GiveWell current recommendation (GW)   
20         GWWC                                           210 GWWC   
21          IGN                    829 Iodine Global Network (IGN)   
22        JHCHS       831 Johns Hopkins Center for Health Security   
23         LTFF                          234 Long-term Future Fund   
24           MC                             833 Malaria Consortium   
25          PHC                 837 Project Healthy Children (PHC)   
26           RC                                839 Rethink Charity   
27          SCI       841 Schistosomiasis Control Initiative (SCI)   
28           SI                       842 Sentience Institute (SI)   
29           SS                        843 Sightsavers (deworming)   
30           Un                                   000 Unrestricted   
31          WAI                         846 Wild Animal Initiative   
32        GWAGF                     867 GiveWell (All Grants Fund)   
33          LLF                      237 Longview Longtermism Fund   
34        ACE R  802 ACE Recommendations - Animal Charity Evalu...   
35        ACE M  851 ACE Movement Grants - Animal Charity Evalu...   
36        FP GC  865 Founders Pledge Global Catastrophic Risks ...   
37          ACX                                     857 ACX Grants   
38          GEC                         872 Good Energy Collective   
39           IL                               875 Industrious Labs   

             restriction                                     parfitslug  
0   EA Funds Grantmaking                     against-malaria-foundation  
1     80,000 Hours (80K)                                    80000-hours  
2   EA Funds Grantmaking        alliance-to-feed-the-earth-in-disasters  
3   EA Funds Grantmaking                                 animal-welfare  
4   EA Funds Grantmaking                           clean-air-task-force  
5                   CEA                   centre-for-effective-altruism  
6   EA Funds Grantmaking              charity-entrepreneurship-projects  
7                    CEA                                                 
8   EA Funds Grantmaking             stiftung-fur-effektiven-altruismus  
9   EA Funds Grantmaking                development-media-international  
10  EA Funds Grantmaking                    deworm-the-world-initiative  
11  EA Funds Grantmaking                                   ea-community  
12  EA Funds Grantmaking                                       end-fund  
13  EA Funds Grantmaking            founders-pledge-climate-change-fund  
14  EA Funds Grantmaki

In [310]:
df.loc[df.last_name == "Dinwoodie"].head(1)

payout_id recipient   gateway             invoice_date currency_code  \
62  944HSFWVBH    cea-uk  Benevity  Sat 10 Dec 2022 0:00:00           GBP   

   amount                     email first_name  last_name  \
62    200  ADINWOODIE@microsoft.com       Adam  Dinwoodie   

                address  ...  ACX  GEC   IL donor_match restriction  \
62  Not shared by donor  ...  NaN  NaN  NaN         Yes    EA Funds   

                        project multiple    flag allocation_sum_check  \
62  233 Global Development Fund       No  Review                    1   

   sum_check  
62       1.0  

[1 rows x 81 columns]

### JSON mapping (row by row)

Then map the parfit slug (we want to do this after editing has happened)

In [311]:
import pandas as pd
import json
import math

# Assuming your DataFrame is named df
# Assuming the reference table is named ref

# Create a dictionary mapping the abbreviation to parfitslug from the reference table
allocation_mapping = dict(zip(ref['abbreviation'], ref['parfitslug']))

# Group the DataFrame by 'payout_id'
grouped = df.groupby('payout_id')

# Initialize the JSON structure
json_structure = []

# Iterate over the groups
for payout_id, group in grouped:
    # Create a payment list for each payout ID
    payments = []

    # Convert the DataFrame to a JSON object
    for _, row in group.iterrows():
        allocation = []
        for col in group.loc[:, 'GHDF':'IL']:
            organization = allocation_mapping.get(col)
            percentage = row[col]
            if organization and not math.isnan(percentage) and percentage != 0:
                allocation.append({
                    "percentage": percentage,
                    "organization": organization
                })
        payment = {
            "person": {
                "email": row["email"],
                "first_name": row["first_name"],
                "last_name": row["last_name"],
                "address": row["address"],
                "city": row["city"],
                "state": row["state"],
                "postal_code": row["postal_code"],
                "country": row["country"]
            },
            "charge_currency_code": row["charge_currency_code"],
            "charge_amount": row["charge_amount"],
            "matched_amount": row["matched_amount"],
            "currency_code": row["currency_code"],
            "fee": row["fee"],
            "recipient": row["recipient"],
            "allocation": allocation,
            "gateway": row["gateway"],
            "payment_method": row["payment_method"],
            "donated_at": row["donated_at"],
            "metadata": {
                "matching": {
                    "type": "company_matching",
                    "company_name": row["matching_company_name"]
                },
                "benevity": {
                    "cause_support_fee": row["cause_support_fee"],
                    "comment": row["comment"],
                    "company": row["matching_company_name"],
                    "fee_comment": row["fee_comment"],
                    "merchant_fee": row["merchant_fee"],
                    "project_remote": row["project_remote"],
                    "reason": row["reason"],
                    "source": row["source"]
                }
            },
            "amount": row["amount"],
            "net": row["net"]
        }
        payments.append(payment)

    # Create a dictionary for each payout ID and its corresponding payments
    payout_dict = {
        "payout_id": payout_id,
        "recipient": group['recipient'].iloc[0],
        "gateway": group['gateway'].iloc[0],
        "invoice_date": group['invoice_date'].iloc[0],
        "currency_code": group['currency_code'].iloc[0],
        "amount": None,  # Placeholder for the amount, leave it blank for now
        "payments": payments
    }

    # Append the payout dictionary to the JSON structure list
    json_structure.append(payout_dict)

# Convert the JSON structure to a JSON string
json_data = json.dumps(json_structure, indent=4, default=str)



In [312]:
# Print the first entry and its first payment entry
first_entry = json_structure[0]
first_payment = first_entry["payments"][0]

print("First Entry:")
print(json.dumps(first_entry, indent=4, default=str))

First Entry:
{
    "payout_id": "944HSFWVBH",
    "recipient": "cea-uk",
    "gateway": "Benevity",
    "invoice_date": "Sat 10 Dec 2022 0:00:00",
    "currency_code": "GBP",
    "amount": null,
    "payments": [
        {
            "person": {
                "email": "r.abernethy@elsevier.com",
                "first_name": "Robert",
                "last_name": "Abernethy",
                "address": "22 Stevenson Crescent",
                "city": "Oxford",
                "state": "Oxfordshire",
                "postal_code": "OX3 9GR",
                "country": "UK"
            },
            "charge_currency_code": "GBP",
            "charge_amount": "0",
            "matched_amount": "750",
            "currency_code": "GBP",
            "fee": "0",
            "recipient": "cea-uk",
            "allocation": [
                {
                    "percentage": 1.0,
                    "organization": "ev-unrestricted"
                }
            ],
            "gateway":